In [1]:
import unicodedata
import re
import os
import json
import requests
from bs4 import BeautifulSoup 

import nltk
from nltk.tokenize.toktok import ToktokTokenizer
from nltk.corpus import stopwords

import pandas as pd
import numpy as np

import acquire as a

In [2]:
##### Imports #####
import unicodedata
import re
import os
import json
import requests
from bs4 import BeautifulSoup 

import nltk
from nltk.tokenize.toktok import ToktokTokenizer
from nltk.corpus import stopwords

import pandas as pd
import numpy as np

import acquire as a


##### Funcitons #####

def basic_clean(string):
    article = string.lower()
    article = unicodedata.normalize('NFKD', article).encode('ascii', 'ignore').decode('utf-8')
    #article = re.sub(r"[^\w]", ' ', article)
    article = re.sub("[^a-z0-9'\s]", '', article)
    article = re.sub("\\n", ' ', article)

    return article

def basic_clean2(string):
    article = string.lower()
    article = unicodedata.normalize('NFKD', article).encode('ascii', 'ignore').decode('utf-8')
    #article = re.sub(r"[^\w]", ' ', article)
    article = re.sub("[^a-z0-9\s]", '', article)
    article = re.sub("\\n", ' ', article)

    return article

def tokenize(string):
    article = []
    # Create the tokenizer
    tokenizer = nltk.tokenize.ToktokTokenizer()

    # Use the tokenizer
    article = tokenizer.tokenize(string, return_str = True)

    return article


def stem(string):
    ps = nltk.porter.PorterStemmer()
    stems = [ps.stem(word) for word in string.split()]
    article_stemmed = ' '.join(stems)
    
    return article_stemmed


def lemmatize(text):
    # Create the Lemmatizer.
    wnl = nltk.stem.WordNetLemmatizer()
    # use the lemmatizer
    lemmas = [wnl.lemmatize(word) for word in text.split()]
    # Join the lemmatized words together
    article_lemmatized = ' '.join(lemmas)
    
    return article_lemmatized


def remove_stopwords(string, extra_words=[], exclude_words=[]):   
    stopword_list = stopwords.words('english')
    # Remove 'exclude_words' from stopword_list to keep these in my text.
    stopword_list = set(stopword_list) - set(exclude_words)
    # Add in 'extra_words' to stopword_list.
    stopword_list = stopword_list.union(set(extra_words))
    # Split words in lemmatized article.
    words = string.split()
    # Iterate through the words and only keep those not in stopword_list
    filtered_words = [word for word in words if word not in stopword_list]
    # Join words in the list back into strings; assign to a variable to keep changes.
    article_without_stopwords = ' '.join(filtered_words)

    return article_without_stopwords

In [3]:
nltk.download('stopwords')
nltk.download('wordnet')

[nltk_data] Downloading package stopwords to
[nltk_data]     /Users/jasontellez/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!
[nltk_data] Downloading package wordnet to
[nltk_data]     /Users/jasontellez/nltk_data...
[nltk_data]   Package wordnet is already up-to-date!


True

In [4]:
df = pd.read_json('data.json')
df

repo          language  \
0               microsoft/react-native-windows               C++   
1                               microsoft/fast        TypeScript   
2     microsoft/Application-Insights-Workbooks              JSON   
3                          microsoft/gctoolkit              Java   
4              microsoft/winget-cli-restsource                C#   
...                                        ...               ...   
1495          microsoft/AzureClusterlessHPC.jl             Julia   
1496             microsoft/multicluster-gitops             Shell   
1497               microsoft/kfp-event-handler                Go   
1498           microsoft/Build-Docker-Provider             Shell   
1499                    microsoft/sqlworkshops  Jupyter Notebook   

                                        readme_contents  
0     <h1 align="center"> React Native for Windows <...  
1     \n![fast_banner_github_914.png](https://static...  
2     # Azure Monitor Workbook Templates [![Build St...  
3     # Microsoft GCToolKit\n\nGCToolkit is a set of...  
4     # Welcome to the winget-cli-restsource reposit...  
...                                                 ...  
1495  [![](https://img.shields.io/badge/docs-stable-...  
1496  # Multi-cluster and multi-tenant environment w...  
1497  # Kubeflow Pipelines Event Handler\n\nThis mic...  
1498  # Build-Docker-Provider\nSuperproject for Dock...  
1499  <img style="float: right;" src="./graphics/sol...  

[1500 rows x 3 columns]

In [5]:
df['clean'] = df['readme_contents'].apply(basic_clean).apply(tokenize).apply(lemmatize).apply(remove_stopwords, extra_words=['build', 'file', 'example', 'code', 'use', 'using'], exclude_words=[])
df

repo          language  \
0               microsoft/react-native-windows               C++   
1                               microsoft/fast        TypeScript   
2     microsoft/Application-Insights-Workbooks              JSON   
3                          microsoft/gctoolkit              Java   
4              microsoft/winget-cli-restsource                C#   
...                                        ...               ...   
1495          microsoft/AzureClusterlessHPC.jl             Julia   
1496             microsoft/multicluster-gitops             Shell   
1497               microsoft/kfp-event-handler                Go   
1498           microsoft/Build-Docker-Provider             Shell   
1499                    microsoft/sqlworkshops  Jupyter Notebook   

                                        readme_contents  \
0     <h1 align="center"> React Native for Windows <...   
1     \n![fast_banner_github_914.png](https://static...   
2     # Azure Monitor Workbook Templates [![Build St...   
3     # Microsoft GCToolKit\n\nGCToolkit is a set of...   
4     # Welcome to the winget-cli-restsource reposit...   
...                                                 ...   
1495  [![](https://img.shields.io/badge/docs-stable-...   
1496  # Multi-cluster and multi-tenant environment w...   
1497  # Kubeflow Pipelines Event Handler\n\nThis mic...   
1498  # Build-Docker-Provider\nSuperproject for Dock...   
1499  <img style="float: right;" src="./graphics/sol...   

                                                  clean  
0     h1 aligncenter react native window h1 p alignc...  
1     fastbannergithub914pnghttpsstaticfastdesignass...  
2     azure monitor workbook template statushttpsgit...  
3     microsoft gctoolkit gctoolkit set library anal...  
4     welcome wingetclirestsource repository buildin...  
...                                                 ...  
1495  httpsimgshieldsiobadgedocsstablebluesvghttpsmi...  
1496  multicluster multitenant environment flux v2 r...  
1497  kubeflow pipeline event handler microservice e...  
1498  builddockerprovider superproject dockerprovide...  
1499  img stylefloat right srcgraphicssolutionsmicro...  

[1500 rows x 4 columns]

In [6]:
df.clean = df.clean.str.strip()
df

repo          language  \
0               microsoft/react-native-windows               C++   
1                               microsoft/fast        TypeScript   
2     microsoft/Application-Insights-Workbooks              JSON   
3                          microsoft/gctoolkit              Java   
4              microsoft/winget-cli-restsource                C#   
...                                        ...               ...   
1495          microsoft/AzureClusterlessHPC.jl             Julia   
1496             microsoft/multicluster-gitops             Shell   
1497               microsoft/kfp-event-handler                Go   
1498           microsoft/Build-Docker-Provider             Shell   
1499                    microsoft/sqlworkshops  Jupyter Notebook   

                                        readme_contents  \
0     <h1 align="center"> React Native for Windows <...   
1     \n![fast_banner_github_914.png](https://static...   
2     # Azure Monitor Workbook Templates [![Build St...   
3     # Microsoft GCToolKit\n\nGCToolkit is a set of...   
4     # Welcome to the winget-cli-restsource reposit...   
...                                                 ...   
1495  [![](https://img.shields.io/badge/docs-stable-...   
1496  # Multi-cluster and multi-tenant environment w...   
1497  # Kubeflow Pipelines Event Handler\n\nThis mic...   
1498  # Build-Docker-Provider\nSuperproject for Dock...   
1499  <img style="float: right;" src="./graphics/sol...   

                                                  clean  
0     h1 aligncenter react native window h1 p alignc...  
1     fastbannergithub914pnghttpsstaticfastdesignass...  
2     azure monitor workbook template statushttpsgit...  
3     microsoft gctoolkit gctoolkit set library anal...  
4     welcome wingetclirestsource repository buildin...  
...                                                 ...  
1495  httpsimgshieldsiobadgedocsstablebluesvghttpsmi...  
1496  multicluster multitenant environment flux v2 r...  
1497  kubeflow pipeline event handler microservice e...  
1498  builddockerprovider superproject dockerprovide...  
1499  img stylefloat right srcgraphicssolutionsmicro...  

[1500 rows x 4 columns]

In [7]:
soup = BeautifulSoup(df.readme_contents[1499], 'html.parser')
print(soup.prettify())

<img src="./graphics/solutions-microsoft-logo-small.png" style="float: right;"/>
# SQL Server and Azure SQL Labs and Workshops
## (https://aka.ms/sqlworkshops)

This [site](https://lab.github.com/githubtraining/introduction-to-github) is a map of learning content produced by and curated by the SQL Server and Azure SQL teams in Microsoft Engineering. These materials are meant to be instructor-led, but you can work through the materials on a test system on your own if desired. Labs are shorter and Workshops are more comprehensive. You can view all materials directly in this interface, or you can [view the raw github site for this content here](https://github.com/Microsoft/sqlworkshops).

To download a Workshop or Lab to your local computer, navigate to the Workshop or Lab's *github page* using the links below. Once there, click the **Clone or Download** button you see there. [More about that process is here](https://help.github.com/en/github/creating-cloning-and-archiving-repositories/cl

In [8]:
soup.text

'\n\n# SQL Server and Azure SQL Labs and Workshops\n## (https://aka.ms/sqlworkshops)\n\nThis [site](https://lab.github.com/githubtraining/introduction-to-github) is a map of learning content produced by and curated by the SQL Server and Azure SQL teams in Microsoft Engineering. These materials are meant to be instructor-led, but you can work through the materials on a test system on your own if desired. Labs are shorter and Workshops are more comprehensive. You can view all materials directly in this interface, or you can [view the raw github site for this content here](https://github.com/Microsoft/sqlworkshops).\n\nTo download a Workshop or Lab to your local computer, navigate to the Workshop or Lab\'s *github page* using the links below. Once there, click the **Clone or Download** button you see there. [More about that process is here](https://help.github.com/en/github/creating-cloning-and-archiving-repositories/cloning-a-repository). \n\n*See the license information at the bottom of

In [9]:
x = [basic_clean2(tokenize(basic_clean(BeautifulSoup(readme_contents, 'html.parser').text))) for readme_contents in df.readme_contents]
x

['react native for windows build native windows apps with react hero image with logohttpsgithubcommicrosoftreactnativewindowsrawmaingithubhero2png see the official react native websitehttpsreactnativedev for an introduction to react native react nativehttpsreactnativedev is a framework developed by facebook that enables you to build worldclass application experiences on native platforms using a consistent developer experience based on javascript and reacthttpsreactjsorg the focus of react native is on developer efficiency across all the platforms you care about learn once write anywhere this repository adds support for the windows 10 sdkhttpsdevelopermicrosoftcomenuswindowsdownloads which allows you to build apps for all devices supported by windows 10httpsdevelopermicrosoftcomenuswindowsgetstartedwindows10 including pcs tablets 2in1s xbox mixed reality devices etc visit the official react native for windows macos websitehttpsmicrosoftgithubioreactnativewindows to learn more contents r

In [10]:
df = df.reset_index(drop=True)

In [11]:
df['clean_without_html'] = pd.Series(x)

In [12]:
df.tail()

repo          language  \
1495  microsoft/AzureClusterlessHPC.jl             Julia   
1496     microsoft/multicluster-gitops             Shell   
1497       microsoft/kfp-event-handler                Go   
1498   microsoft/Build-Docker-Provider             Shell   
1499            microsoft/sqlworkshops  Jupyter Notebook   

                                        readme_contents  \
1495  [![](https://img.shields.io/badge/docs-stable-...   
1496  # Multi-cluster and multi-tenant environment w...   
1497  # Kubeflow Pipelines Event Handler\n\nThis mic...   
1498  # Build-Docker-Provider\nSuperproject for Dock...   
1499  <img style="float: right;" src="./graphics/sol...   

                                                  clean  \
1495  httpsimgshieldsiobadgedocsstablebluesvghttpsmi...   
1496  multicluster multitenant environment flux v2 r...   
1497  kubeflow pipeline event handler microservice e...   
1498  builddockerprovider superproject dockerprovide...   
1499  img stylefloat right srcgraphicssolutionsmicro...   

                                     clean_without_html  
1495  httpsimgshieldsiobadgedocsstablebluesvghttpsmi...  
1496  multicluster and multitenant environment with ...  
1497  kubeflow pipelines event handler this microser...  
1498  builddockerprovider superproject for dockerpro...  
1499  sql server and azure sql labs and workshops ht...

In [13]:
df.dropna(subset=['language'], inplace=True)

In [14]:
df.isnull().sum()

repo                  0
language              0
readme_contents       0
clean                 0
clean_without_html    0
dtype: int64

In [23]:
df.drop(index=df.loc[df['clean'] == df['clean_without_html']].index, inplace=True)

In [24]:
df.reset_index(drop=True)

repo          language  \
0               microsoft/react-native-windows               C++   
1                               microsoft/fast        TypeScript   
2     microsoft/Application-Insights-Workbooks              JSON   
3                          microsoft/gctoolkit              Java   
4              microsoft/winget-cli-restsource                C#   
...                                        ...               ...   
1365          microsoft/AzureClusterlessHPC.jl             Julia   
1366             microsoft/multicluster-gitops             Shell   
1367               microsoft/kfp-event-handler                Go   
1368           microsoft/Build-Docker-Provider             Shell   
1369                    microsoft/sqlworkshops  Jupyter Notebook   

                                        readme_contents  \
0     <h1 align="center"> React Native for Windows <...   
1     \n![fast_banner_github_914.png](https://static...   
2     # Azure Monitor Workbook Templates [![Build St...   
3     # Microsoft GCToolKit\n\nGCToolkit is a set of...   
4     # Welcome to the winget-cli-restsource reposit...   
...                                                 ...   
1365  [![](https://img.shields.io/badge/docs-stable-...   
1366  # Multi-cluster and multi-tenant environment w...   
1367  # Kubeflow Pipelines Event Handler\n\nThis mic...   
1368  # Build-Docker-Provider\nSuperproject for Dock...   
1369  <img style="float: right;" src="./graphics/sol...   

                                                  clean  \
0     h1 aligncenter react native window h1 p alignc...   
1     fastbannergithub914pnghttpsstaticfastdesignass...   
2     azure monitor workbook template statushttpsgit...   
3     microsoft gctoolkit gctoolkit set library anal...   
4     welcome wingetclirestsource repository buildin...   
...                                                 ...   
1365  httpsimgshieldsiobadgedocsstablebluesvghttpsmi...   
1366  multicluster multitenant environment flux v2 r...   
1367  kubeflow pipeline event handler microservice e...   
1368  builddockerprovider superproject dockerprovide...   
1369  img stylefloat right srcgraphicssolutionsmicro...   

                                     clean_without_html  \
0     react native for windows build native windows ...   
1     fastbannergithub914pnghttpsstaticfastdesignass...   
2     azure monitor workbook templates build statush...   
3     microsoft gctoolkit gctoolkit is a set of libr...   
4     welcome to the wingetclirestsource repository ...   
...                                                 ...   
1365  httpsimgshieldsiobadgedocsstablebluesvghttpsmi...   
1366  multicluster and multitenant environment with ...   
1367  kubeflow pipelines event handler this microser...   
1368  builddockerprovider superproject for dockerpro...   
1369  sql server and azure sql labs and workshops ht...   

                                     lemma_no_stopwords  clean_word_count  \
0     react native window native window apps react h...               536   
1     fastbannergithub914pnghttpsstaticfastdesignass...               981   
2     azure monitor workbook template statushttpsgit...               385   
3     microsoft gctoolkit gctoolkit set library anal...               349   
4     welcome wingetclirestsource repository buildin...               780   
...                                                 ...               ...   
1365  httpsimgshieldsiobadgedocsstablebluesvghttpsmi...               277   
1366  multicluster multitenant environment flux v2 r...              1698   
1367  kubeflow pipeline event handler microservice e...               350   
1368  builddockerprovider superproject dockerprovide...               457   
1369  sql server azure sql lab workshop httpsakamssq...               606   

      readme_char_count  
0                  4288  
1                  8539  
2                  3411  
3                  2815  
4                  5557  
...              

In [25]:
df['lemma_no_stopwords'] = df.clean_without_html.apply(lemmatize).apply(remove_stopwords, extra_words=['build', 'file', 'example', 'code', 'use', 'using'], exclude_words=[])

In [26]:
df.loc[df['clean'] == df['clean_without_html']]

Empty DataFrame
Columns: [repo, language, readme_contents, clean, clean_without_html, lemma_no_stopwords, clean_word_count, readme_char_count]
Index: []

In [27]:
df.loc[df['lemma_no_stopwords'] == df['clean_without_html']]

Empty DataFrame
Columns: [repo, language, readme_contents, clean, clean_without_html, lemma_no_stopwords, clean_word_count, readme_char_count]
Index: []

In [28]:
df.head()

repo    language  \
0            microsoft/react-native-windows         C++   
1                            microsoft/fast  TypeScript   
2  microsoft/Application-Insights-Workbooks        JSON   
3                       microsoft/gctoolkit        Java   
4           microsoft/winget-cli-restsource          C#   

                                     readme_contents  \
0  <h1 align="center"> React Native for Windows <...   
1  \n![fast_banner_github_914.png](https://static...   
2  # Azure Monitor Workbook Templates [![Build St...   
3  # Microsoft GCToolKit\n\nGCToolkit is a set of...   
4  # Welcome to the winget-cli-restsource reposit...   

                                               clean  \
0  h1 aligncenter react native window h1 p alignc...   
1  fastbannergithub914pnghttpsstaticfastdesignass...   
2  azure monitor workbook template statushttpsgit...   
3  microsoft gctoolkit gctoolkit set library anal...   
4  welcome wingetclirestsource repository buildin...   

                                  clean_without_html  \
0  react native for windows build native windows ...   
1  fastbannergithub914pnghttpsstaticfastdesignass...   
2  azure monitor workbook templates build statush...   
3  microsoft gctoolkit gctoolkit is a set of libr...   
4  welcome to the wingetclirestsource repository ...   

                                  lemma_no_stopwords  clean_word_count  \
0  react native window native window apps react h...               536   
1  fastbannergithub914pnghttpsstaticfastdesignass...               981   
2  azure monitor workbook template statushttpsgit...               385   
3  microsoft gctoolkit gctoolkit set library anal...               349   
4  welcome wingetclirestsource repository buildin...               780   

   readme_char_count  
0               4288  
1               8539  
2               3411  
3               2815  
4               5557

In [29]:
df['clean_word_count'] = df.clean_without_html.str.split().str.len()
df.head()

repo    language  \
0            microsoft/react-native-windows         C++   
1                            microsoft/fast  TypeScript   
2  microsoft/Application-Insights-Workbooks        JSON   
3                       microsoft/gctoolkit        Java   
4           microsoft/winget-cli-restsource          C#   

                                     readme_contents  \
0  <h1 align="center"> React Native for Windows <...   
1  \n![fast_banner_github_914.png](https://static...   
2  # Azure Monitor Workbook Templates [![Build St...   
3  # Microsoft GCToolKit\n\nGCToolkit is a set of...   
4  # Welcome to the winget-cli-restsource reposit...   

                                               clean  \
0  h1 aligncenter react native window h1 p alignc...   
1  fastbannergithub914pnghttpsstaticfastdesignass...   
2  azure monitor workbook template statushttpsgit...   
3  microsoft gctoolkit gctoolkit set library anal...   
4  welcome wingetclirestsource repository buildin...   

                                  clean_without_html  \
0  react native for windows build native windows ...   
1  fastbannergithub914pnghttpsstaticfastdesignass...   
2  azure monitor workbook templates build statush...   
3  microsoft gctoolkit gctoolkit is a set of libr...   
4  welcome to the wingetclirestsource repository ...   

                                  lemma_no_stopwords  clean_word_count  \
0  react native window native window apps react h...               536   
1  fastbannergithub914pnghttpsstaticfastdesignass...               981   
2  azure monitor workbook template statushttpsgit...               385   
3  microsoft gctoolkit gctoolkit set library anal...               349   
4  welcome wingetclirestsource repository buildin...               780   

   readme_char_count  
0               4288  
1               8539  
2               3411  
3               2815  
4               5557

In [30]:
df['readme_char_count'] = df.clean_without_html.str.len()
df.head()

repo    language  \
0            microsoft/react-native-windows         C++   
1                            microsoft/fast  TypeScript   
2  microsoft/Application-Insights-Workbooks        JSON   
3                       microsoft/gctoolkit        Java   
4           microsoft/winget-cli-restsource          C#   

                                     readme_contents  \
0  <h1 align="center"> React Native for Windows <...   
1  \n![fast_banner_github_914.png](https://static...   
2  # Azure Monitor Workbook Templates [![Build St...   
3  # Microsoft GCToolKit\n\nGCToolkit is a set of...   
4  # Welcome to the winget-cli-restsource reposit...   

                                               clean  \
0  h1 aligncenter react native window h1 p alignc...   
1  fastbannergithub914pnghttpsstaticfastdesignass...   
2  azure monitor workbook template statushttpsgit...   
3  microsoft gctoolkit gctoolkit set library anal...   
4  welcome wingetclirestsource repository buildin...   

                                  clean_without_html  \
0  react native for windows build native windows ...   
1  fastbannergithub914pnghttpsstaticfastdesignass...   
2  azure monitor workbook templates build statush...   
3  microsoft gctoolkit gctoolkit is a set of libr...   
4  welcome to the wingetclirestsource repository ...   

                                  lemma_no_stopwords  clean_word_count  \
0  react native window native window apps react h...               536   
1  fastbannergithub914pnghttpsstaticfastdesignass...               981   
2  azure monitor workbook template statushttpsgit...               385   
3  microsoft gctoolkit gctoolkit set library anal...               349   
4  welcome wingetclirestsource repository buildin...               780   

   readme_char_count  
0               4288  
1               8539  
2               3411  
3               2815  
4               5557

In [31]:
df['is_TypeScript'] = df.language == 'TypeScript'
df.head()

repo    language  \
0            microsoft/react-native-windows         C++   
1                            microsoft/fast  TypeScript   
2  microsoft/Application-Insights-Workbooks        JSON   
3                       microsoft/gctoolkit        Java   
4           microsoft/winget-cli-restsource          C#   

                                     readme_contents  \
0  <h1 align="center"> React Native for Windows <...   
1  \n![fast_banner_github_914.png](https://static...   
2  # Azure Monitor Workbook Templates [![Build St...   
3  # Microsoft GCToolKit\n\nGCToolkit is a set of...   
4  # Welcome to the winget-cli-restsource reposit...   

                                               clean  \
0  h1 aligncenter react native window h1 p alignc...   
1  fastbannergithub914pnghttpsstaticfastdesignass...   
2  azure monitor workbook template statushttpsgit...   
3  microsoft gctoolkit gctoolkit set library anal...   
4  welcome wingetclirestsource repository buildin...   

                                  clean_without_html  \
0  react native for windows build native windows ...   
1  fastbannergithub914pnghttpsstaticfastdesignass...   
2  azure monitor workbook templates build statush...   
3  microsoft gctoolkit gctoolkit is a set of libr...   
4  welcome to the wingetclirestsource repository ...   

                                  lemma_no_stopwords  clean_word_count  \
0  react native window native window apps react h...               536   
1  fastbannergithub914pnghttpsstaticfastdesignass...               981   
2  azure monitor workbook template statushttpsgit...               385   
3  microsoft gctoolkit gctoolkit set library anal...               349   
4  welcome wingetclirestsource repository buildin...               780   

   readme_char_count  is_TypeScript  
0               4288          False  
1               8539           True  
2               3411          False  
3               2815          False  
4               5557          False

In [32]:
df = df[['repo', 'language', 'clean_without_html', 'lemma_no_stopwords', 'clean_word_count', 'readme_char_count', 'is_TypeScript']]

In [33]:
df.head()

repo    language  \
0            microsoft/react-native-windows         C++   
1                            microsoft/fast  TypeScript   
2  microsoft/Application-Insights-Workbooks        JSON   
3                       microsoft/gctoolkit        Java   
4           microsoft/winget-cli-restsource          C#   

                                  clean_without_html  \
0  react native for windows build native windows ...   
1  fastbannergithub914pnghttpsstaticfastdesignass...   
2  azure monitor workbook templates build statush...   
3  microsoft gctoolkit gctoolkit is a set of libr...   
4  welcome to the wingetclirestsource repository ...   

                                  lemma_no_stopwords  clean_word_count  \
0  react native window native window apps react h...               536   
1  fastbannergithub914pnghttpsstaticfastdesignass...               981   
2  azure monitor workbook template statushttpsgit...               385   
3  microsoft gctoolkit gctoolkit set library anal...               349   
4  welcome wingetclirestsource repository buildin...               780   

   readme_char_count  is_TypeScript  
0               4288          False  
1               8539           True  
2               3411          False  
3               2815          False  
4               5557          False

In [34]:
df = df.rename(columns={"clean_without_html": "clean"})

In [35]:
df = df.reset_index(drop=True)

In [36]:
df

repo          language  \
0               microsoft/react-native-windows               C++   
1                               microsoft/fast        TypeScript   
2     microsoft/Application-Insights-Workbooks              JSON   
3                          microsoft/gctoolkit              Java   
4              microsoft/winget-cli-restsource                C#   
...                                        ...               ...   
1365          microsoft/AzureClusterlessHPC.jl             Julia   
1366             microsoft/multicluster-gitops             Shell   
1367               microsoft/kfp-event-handler                Go   
1368           microsoft/Build-Docker-Provider             Shell   
1369                    microsoft/sqlworkshops  Jupyter Notebook   

                                                  clean  \
0     react native for windows build native windows ...   
1     fastbannergithub914pnghttpsstaticfastdesignass...   
2     azure monitor workbook templates build statush...   
3     microsoft gctoolkit gctoolkit is a set of libr...   
4     welcome to the wingetclirestsource repository ...   
...                                                 ...   
1365  httpsimgshieldsiobadgedocsstablebluesvghttpsmi...   
1366  multicluster and multitenant environment with ...   
1367  kubeflow pipelines event handler this microser...   
1368  builddockerprovider superproject for dockerpro...   
1369  sql server and azure sql labs and workshops ht...   

                                     lemma_no_stopwords  clean_word_count  \
0     react native window native window apps react h...               536   
1     fastbannergithub914pnghttpsstaticfastdesignass...               981   
2     azure monitor workbook template statushttpsgit...               385   
3     microsoft gctoolkit gctoolkit set library anal...               349   
4     welcome wingetclirestsource repository buildin...               780   
...                                                 ...               ...   
1365  httpsimgshieldsiobadgedocsstablebluesvghttpsmi...               277   
1366  multicluster multitenant environment flux v2 r...              1698   
1367  kubeflow pipeline event handler microservice e...               350   
1368  builddockerprovider superproject dockerprovide...               457   
1369  sql server azure sql lab workshop httpsakamssq...               606   

      readme_char_count  is_TypeScript  
0                  4288          False  
1                  8539           True  
2                  3411          False  
3                  2815          False  
4                  5557          False  
...                 ...            ...  
1365               2557          False  
1366              12324          False  
1367               2558          False  
1368               3569          False  
1369               5484          False  

[1370 rows x 7 columns]

In [ ]:
df.to_json('cleaned_readmes.json')